In [43]:
import pandas as pd
import numpy as np
import json
from sklearn.preprocessing import LabelEncoder
from tqdm._tqdm_notebook import tqdm_notebook as bar;
bar().pandas("track progress")

from joblib import Parallel, delayed
from multiprocessing import Pool, cpu_count
import time

label = LabelEncoder()

dir='/Users/xinwang/ai/dataset/kaggle/GStore/'
train_file = 'train.csv'
test_file = 'test.csv'

train = pd.read_csv(dir + train_file, low_memory=False)
test = pd.read_csv(dir + test_file, low_memory=False)

print('train.shape',train.shape)
print('test.shape',test.shape)
print()


cate_features = []
numeric_features = []

train['fullVisitorId'] = train['fullVisitorId'].astype(str)
test['fullVisitorId'] = test['fullVisitorId'].astype(str)

train['channelGrouping'] = label.fit_transform(train['channelGrouping'])
test['channelGrouping'] = label.fit_transform(test['channelGrouping'])

cate_features.append('channelGrouping')

def label_transform(df, col_list):
    for col in col_list:
        df[col] = label.fit_transform(df[col])

    return df

####################################
date_features = ['date','year','month','day','week','weekofyear','dayofweek','quarter','month_start','month_end']

def process_date(df):
    df['date'] = pd.to_datetime(df['date'], format='%Y%m%d',errors='ignore')
    df['year'] = df['date'].dt.year
    df['month'] = df['date'].dt.month
    df['day'] = df['date'].dt.day

    df['week'] = df['date'].dt.week
    df['weekofyear'] = df['date'].dt.weekofyear
    df['dayofweek'] = df['date'].dt.dayofweek
    df['quarter'] = df['date'].dt.quarter
    df['month_start'] = df['date'].dt.is_month_start
    df['month_end'] = df['date'].dt.is_month_end

    df = label_transform(df, date_features)
    
    return df

train = process_date(train)
test = process_date(test)
cate_features += date_features
print('process_date done')


################device####################
device_features = ['browser','operatingSystem','isMobile','deviceCategory']

def process_device(df):
    df['browser'] = df['device'].progress_apply(lambda x: json.loads(x)['browser'])
    df['operatingSystem'] = df['device'].progress_apply(lambda x: json.loads(x)['operatingSystem'])
    df['isMobile'] = df['device'].progress_apply(lambda x: json.loads(x)['isMobile'])
    df['deviceCategory'] = df['device'].progress_apply(lambda x: json.loads(x)['deviceCategory'])

    df = label_transform(df, device_features)

    return df

train = process_device(train)
test = process_device(test)
cate_features += device_features
print('process_device done')


###############geoNetwork#####################
geo_features = ['continent','subContinent','country','region','metro','city','networkDomain']

def process_geo(df):
    df['continent'] = df['geoNetwork'].progress_apply(lambda x: json.loads(x)['continent'])
    df['subContinent'] = df['geoNetwork'].progress_apply(lambda x: json.loads(x)['subContinent'])
    df['country'] = df['geoNetwork'].progress_apply(lambda x: json.loads(x)['country'])
    df['region'] = df['geoNetwork'].progress_apply(lambda x: json.loads(x)['region'])
    df['metro'] = df['geoNetwork'].progress_apply(lambda x: json.loads(x)['metro'])
    df['city'] = df['geoNetwork'].progress_apply(lambda x: json.loads(x)['city'])
    df['networkDomain'] = df['geoNetwork'].progress_apply(lambda x: json.loads(x)['networkDomain'])

    df = label_transform(df, geo_features)

    return df

train = process_geo(train)
test = process_geo(test)
cate_features += geo_features
print('process_geo done')


################totals####################
view_features = ['hits','pageviews','newVisits','bounces','visitNumber']

def process_totals(df):
    df['hits'] = df['totals'].progress_apply(lambda x: json.loads(x)['hits']).astype(int)
    df['pageviews'] = df['totals'].apply(lambda x: json.loads(x)['pageviews'] if x.find('pageviews')>=0 else 0).astype(int)
    df['bounces'] = df['totals'].apply(lambda x: json.loads(x)['bounces'] if x.find('bounces')>=0 else 0).astype(int)
    df['newVisits'] = df['totals'].apply(lambda x: json.loads(x)['newVisits'] if x.find('newVisits')>=0 else 0).astype(int)
    df['transactionRevenue'] = df['totals'].progress_apply(lambda x: json.loads(x)['transactionRevenue'] if x.find('transactionRevenue')>=0 else 0).astype(int)

    return df

train = process_totals(train)
test = process_totals(test)
numeric_features += view_features
print('process_totals done')

################totals####################
last_time_features = ['last_seconds','last_minutes']

def process_last_time(df):
    df['last_seconds'] = df['visitStartTime']-df['visitId']
    df['last_minutes'] = (df['visitStartTime']-df['visitId'])/60
    df['last_minutes'] = df['last_minutes'].astype(np.int64)

    return df

train = process_last_time(train)
test = process_last_time(test)
numeric_features += last_time_features
print('process_last_time done')



train.shape (903653, 12)
test.shape (804684, 12)

process_date done



process_device done



process_geo done



process_totals done
process_last_time done


In [44]:
################Multip transaction####################
def process_transaction_count(df):
    transaction_df = df[['fullVisitorId','transactionRevenue']].groupby('fullVisitorId')
        
    transac_count_df = transaction_df.count()
    transac_count_df['fullVisitorId'] = transac_count_df.index
    transac_count_df.rename(columns={
        'transactionRevenue':'transaction_count'
    }, inplace=True)
    transac_count_df['transaction_count']=transac_count_df['transaction_count'].astype(int)

    df = pd.merge(df, transac_count_df, on='fullVisitorId')

    return df

train = process_transaction_count(train)
test = process_transaction_count(test)
numeric_features.append('transaction_count')
print('process_transaction_count done')

def process_buy_times(df):
    transaction_df = df[['fullVisitorId','transactionRevenue']].groupby('fullVisitorId')

    def count_buy_times(x):
        buy_times = sum(x['transactionRevenue']>0)

        return buy_times

    buy_times_group = transaction_df.progress_apply(count_buy_times)
    buy_times_df = pd.DataFrame({
        'fullVisitorId':buy_times_group.index,
        'buy_times':buy_times_group.values
    })

    df = pd.merge(df, buy_times_df, on='fullVisitorId')

    return df

train = process_buy_times(train)
test = process_buy_times(test)
numeric_features.append('buy_times')
print('process_buy_times done')

/Users/xinwang/ai/lib/python3.6/site-packages/ipykernel_launcher.py:16: FutureWarning: 'fullVisitorId' is both an index level and a column label.
Defaulting to column, but this will raise an ambiguity error in a future version
  app.launch_new_instance()
/Users/xinwang/ai/lib/python3.6/site-packages/ipykernel_launcher.py:17: FutureWarning: 'fullVisitorId' is both an index level and a column label.
Defaulting to column, but this will raise an ambiguity error in a future version


process_transaction_count done



process_buy_times done


In [45]:
def parse_adwordsClickInfo_field(x, field):
    jo = json.loads(x)
    
    if x.find('adwordsClickInfo')>=0:
        adwordsClickInfo = jo['adwordsClickInfo']
        
        if str(adwordsClickInfo).find(field)>=0:
            return adwordsClickInfo[field]

    return 0

def parse_adwordsClickInfo_page(x):
    return parse_adwordsClickInfo_field(x, 'page')

def parse_adwordsClickInfo_slot(x):
    return parse_adwordsClickInfo_field(x, 'slot')

def parse_adwordsClickInfo_gclId(x):
    return parse_adwordsClickInfo_field(x, 'gclId')

def parse_adwordsClickInfo_adNetworkType(x):
    return parse_adwordsClickInfo_field(x, 'adNetworkType')

def parse_adwordsClickInfo_isVideoAd(x):
    return parse_adwordsClickInfo_field(x, 'isVideoAd')

traffic_features = ['campaign','source','medium','keyword','adwordsClickInfo_gclId_prefix','adwordsClickInfo_slot',
                    'adwordsClickInfo_gclId','adwordsClickInfo_adNetworkType']

def process_traffic(df):
    df['campaign'] = df['trafficSource'].progress_apply(lambda x: json.loads(x)['campaign']).astype(str)
    # need to merge nearly same record
    df['source'] = df['trafficSource'].apply(lambda x: json.loads(x)['source']).astype(str)
    df['medium'] = df['trafficSource'].apply(lambda x: json.loads(x)['medium']).astype(str)
    # need to merge some keywords
    df['keyword'] = df['trafficSource'].progress_apply(lambda x: json.loads(x)['keyword'] if x.find('keyword')>=0 else 0).astype(str)

    df['adwordsClickInfo_page'] = df['trafficSource'].apply(parse_adwordsClickInfo_page).astype(int)
    df['adwordsClickInfo_slot'] = df['trafficSource'].apply(parse_adwordsClickInfo_slot).astype(str)
    df['adwordsClickInfo_gclId'] = df['trafficSource'].progress_apply(parse_adwordsClickInfo_gclId).astype(str)
    df['adwordsClickInfo_gclId_prefix'] = df['adwordsClickInfo_gclId'].apply(lambda x: x.split('_')[0] if type(x)!=int and x.find('_')>=0 else 0).astype(str)
    df['adwordsClickInfo_adNetworkType'] = df['trafficSource'].progress_apply(parse_adwordsClickInfo_adNetworkType).astype(str)

    df = label_transform(df, traffic_features)
    
    return df

train = process_traffic(train)
test = process_traffic(test)

cate_features += traffic_features
numeric_features.append('adwordsClickInfo_page')
print('process_traffic done')

###################################################### 
target = 'revenue'

def process_revenue(df):
    revenue_df = df[['fullVisitorId','transactionRevenue']].groupby('fullVisitorId').agg('sum')
    revenue_df['fullVisitorId'] = revenue_df.index
    revenue_df[target] = revenue_df['transactionRevenue'].progress_apply(lambda x: np.log(x+1))

    revenue_df.drop('transactionRevenue', axis=1, inplace=True)
    
    df = pd.merge(df, revenue_df, on='fullVisitorId')

    return df


train = process_revenue(train)
test = process_revenue(test)
print('process_revenue done')

removed_columns = ['sessionId','device','geoNetwork','socialEngagementType','totals','trafficSource','transactionRevenue']
train.drop(removed_columns, axis=1, inplace=True)


print('train.shape',train.shape)
print('test.shape',test.shape)
print()


process_traffic done


/Users/xinwang/ai/lib/python3.6/site-packages/ipykernel_launcher.py:70: FutureWarning: 'fullVisitorId' is both an index level and a column label.
Defaulting to column, but this will raise an ambiguity error in a future version


/Users/xinwang/ai/lib/python3.6/site-packages/ipykernel_launcher.py:71: FutureWarning: 'fullVisitorId' is both an index level and a column label.
Defaulting to column, but this will raise an ambiguity error in a future version


process_revenue done
train.shape (903653, 44)
test.shape (804684, 51)



In [46]:
# agg numeric features
def agg_numeric_feature(df):
    for col in numeric_features:
        temp_df = df[[col,'fullVisitorId']].groupby('fullVisitorId')[col].agg(['min','max','mean','median'])
        temp_df['fullVisitorId'] = temp_df.index
        temp_df.rename(columns={
            'min': col +'_' +'min',
            'max': col +'_' +'max',
            'mean': col +'_' +'mean',
            'median': col +'_' +'median'
        }, inplace=True)

        df = pd.merge(df, temp_df, on='fullVisitorId')
        del temp_df

        print(df.shape)

    return df

train = agg_numeric_feature(train)
test = agg_numeric_feature(test)

train.head()

/Users/xinwang/ai/lib/python3.6/site-packages/ipykernel_launcher.py:20: FutureWarning: 'fullVisitorId' is both an index level and a column label.
Defaulting to column, but this will raise an ambiguity error in a future version


(903653, 48)
(903653, 52)
(903653, 56)
(903653, 60)
(903653, 64)
(903653, 68)
(903653, 72)
(903653, 76)
(903653, 80)
(903653, 84)


/Users/xinwang/ai/lib/python3.6/site-packages/ipykernel_launcher.py:21: FutureWarning: 'fullVisitorId' is both an index level and a column label.
Defaulting to column, but this will raise an ambiguity error in a future version


(804684, 55)
(804684, 59)
(804684, 63)
(804684, 67)
(804684, 71)
(804684, 75)
(804684, 79)
(804684, 83)
(804684, 87)
(804684, 91)


channelGrouping  date        fullVisitorId     visitId  visitNumber  \
0                4    32  1131660440785968503  1472830385            1   
1                4    32   377306020877927890  1472880147            1   
2                4    32  3895546263509774583  1472865386            1   
3                4    32  4763447161404445595  1472881213            1   
4                4    32    27294437909732085  1472822600            2   

   visitStartTime  year  month  day  week              ...               \
0      1472830385     0      8    1    34              ...                
1      1472880147     0      8    1    34              ...                
2      1472865386     0      8    1    34              ...                
3      1472881213     0      8    1    34              ...                
4      1472822600     0      8    1    34              ...                

   transaction_count_mean  transaction_count_median  buy_times_min  \
0                       1                         1              0   
1                       1                         1              0   
2                       1                         1              0   
3                       1                         1              0   
4                       2                         2              0   

   buy_times_max  buy_times_mean  buy_times_median  adwordsClickInfo_page_min  \
0              0               0                 0                          0   
1              0               0                 0                          0   
2              0               0                 0                          0   
3              0               0                 0                          0   
4              0               0                 0                          0   

   adwordsClickInfo_page_max  adwordsClickInfo_page_mean  \
0                          0                         0.0   
1                          0                         0.0   
2                          0                         0.0   
3                          0                         0.0   
4                          0                         0.0   

   adwordsClickInfo_page_median  
0                           0.0  
1                           0.0  
2                           0.0  
3                           0.0  
4                           0.0  

[5 rows x 84 columns]

In [48]:
# agg cate features
from pandas import Series
import tqdm

print('train.shape',train.shape)
print('test.shape',test.shape)

def applyParallel(dfGrouped, func, total):
    with Pool(cpu_count()) as p:
        ret_list = list(tqdm.tqdm(p.imap(func, [group for name, group in dfGrouped]),
                                  total=total)) 

    df = pd.concat(ret_list, axis=1)
    df = df.T
    return df


def agg_cate_group_func(group_df):
    new_row = Series()
    new_row['fullVisitorId'] = group_df['fullVisitorId'].values[0]

    for col in cate_features:
        value_counts_series = group_df[col].value_counts()
        
        counts_array = value_counts_series.values
        if len(counts_array)==1:
            new_row[col + '_top_1'] = counts_array[0]
            new_row[col + '_top_2'] = counts_array[0] 
            new_row[col + '_top_3'] = counts_array[0]
        elif len(counts_array)==2:
            new_row[col + '_top_1'] = counts_array[0]
            new_row[col + '_top_2'] = counts_array[1] 
            new_row[col + '_top_3'] = counts_array[1]
        else:
            new_row[col + '_top_1'] = counts_array[0]
            new_row[col + '_top_2'] = counts_array[1] 
            new_row[col + '_top_3'] = counts_array[2]
    return new_row


def expand_cate_features(df):
    d_rows = df[df['fullVisitorId'].duplicated(keep=False)]
    revisted_df = df.loc[d_rows.index]
    
    total = len(revisted_df['fullVisitorId'].unique())
    print('revisted_df',total,revisted_df.shape)
    
    cate_group_data = revisted_df[cate_features + ['fullVisitorId']].groupby('fullVisitorId')

    revisted_cates_top_3_df = applyParallel(cate_group_data, agg_cate_group_func, total)
    print('got revisted_cates_top_3_df', revisted_cates_top_3_df.shape)

    df = pd.merge(df, revisted_cates_top_3_df, on='fullVisitorId', how='left')
    print('df merge cate_top_3_features_df done')
    
    del cate_group_data
    del revisted_cates_top_3_df

    return df
    
train = expand_cate_features(train)
test = expand_cate_features(test)

print('process expand_cate_features done')
print('train.shape',train.shape)
print('test.shape',test.shape)


###################cate_features_fillna########################## 
def cate_features_fillna(df):
    for col in cate_features:
        top_1_null_index = df[df[col + '_top_1'].isnull()].index
        df[col + '_top_1'].fillna(
            df[col].loc[top_1_null_index], inplace=True)
        
        top_2_null_index = df[df[col + '_top_2'].isnull()].index
        df[col + '_top_2'].fillna(
            df[col].loc[top_2_null_index], inplace=True)
        
        top_3_null_index = df[df[col + '_top_3'].isnull()].index
        df[col + '_top_3'].fillna(
            df[col].loc[top_3_null_index], inplace=True)
        print('cate_features_fillna', col)
        
        
    return df
        
        
train = cate_features_fillna(train)
test = cate_features_fillna(test)
print('process cate_features_fillna done')

train.shape (903653, 84)
test.shape (804684, 91)
revisted_df 93492 (282978, 84)



 11%|█▏        | 10545/93492 [4:18:18<33:51:52,  1.47s/it]

  0%|          | 0/93492 [00:00<?, ?it/s]

  0%|          | 1/93492 [00:00<4:39:27,  5.58it/s]

  0%|          | 9/93492 [00:00<1:02:32, 24.91it/s]

  0%|          | 17/93492 [00:00<50:23, 30.92it/s] 

  0%|          | 25/93492 [00:00<45:04, 34.57it/s]

  0%|          | 33/93492 [00:00<43:42, 35.64it/s]

  0%|          | 41/93492 [00:01<41:44, 37.31it/s]

  0%|          | 49/93492 [00:01<40:32, 38.42it/s]

  0%|          | 57/93492 [00:01<39:38, 39.28it/s]

  0%|          | 65/93492 [00:01<39:08, 39.78it/s]

  0%|          | 73/93492 [00:01<38:40, 40.26it/s]

  0%|          | 81/93492 [00:02<38:31, 40.42it/s]

  0%|          | 89/93492 [00:02<37:50, 41.14it/s]

  0%|          | 97/93492 [00:02<37:53, 41.07it/s]

  0%|          | 105/93492 [00:02<37:49, 41.14it/s]

  0%|          | 113/93492 [00:02<37:38, 41.34it/s]

  0%|          | 121/93492 [00:02<37:25, 41.57it/s]

  0%|          | 129/93492 [00:03<37:01, 42.03it/s]

  0%|

  1%|          | 788/93492 [00:18<37:09, 41.58it/s]

  1%|          | 794/93492 [00:19<37:07, 41.61it/s]

  1%|          | 800/93492 [00:19<37:03, 41.69it/s]

  1%|          | 805/93492 [00:19<37:02, 41.71it/s]

  1%|          | 810/93492 [00:19<37:01, 41.73it/s]

  1%|          | 816/93492 [00:19<36:56, 41.81it/s]

  1%|          | 821/93492 [00:19<36:57, 41.79it/s]

  1%|          | 826/93492 [00:19<36:56, 41.81it/s]

  1%|          | 832/93492 [00:19<36:55, 41.83it/s]

  1%|          | 837/93492 [00:20<36:55, 41.82it/s]

  1%|          | 842/93492 [00:20<36:54, 41.84it/s]

  1%|          | 848/93492 [00:20<36:51, 41.88it/s]

  1%|          | 853/93492 [00:20<36:51, 41.89it/s]

  1%|          | 858/93492 [00:20<36:50, 41.91it/s]

  1%|          | 864/93492 [00:20<36:45, 41.99it/s]

  1%|          | 869/93492 [00:20<36:46, 41.98it/s]

  1%|          | 874/93492 [00:20<36:45, 41.99it/s]

  1%|          | 879/93492 [00:20<36:44, 42.02it/s]

  1%|          | 884/93492 [00:21<36:45, 41.99

  2%|▏         | 1570/93492 [00:36<35:36, 43.02it/s]

  2%|▏         | 1575/93492 [00:36<35:36, 43.03it/s]

  2%|▏         | 1580/93492 [00:36<35:38, 42.99it/s]

  2%|▏         | 1586/93492 [00:36<35:35, 43.03it/s]

  2%|▏         | 1591/93492 [00:36<35:35, 43.03it/s]

  2%|▏         | 1596/93492 [00:37<35:37, 42.99it/s]

  2%|▏         | 1601/93492 [00:37<35:36, 43.01it/s]

  2%|▏         | 1607/93492 [00:37<35:34, 43.04it/s]

  2%|▏         | 1612/93492 [00:37<35:36, 43.00it/s]

  2%|▏         | 1618/93492 [00:37<35:34, 43.04it/s]

  2%|▏         | 1623/93492 [00:37<35:33, 43.05it/s]

  2%|▏         | 1628/93492 [00:37<35:35, 43.01it/s]

  2%|▏         | 1633/93492 [00:37<35:34, 43.03it/s]

  2%|▏         | 1639/93492 [00:38<35:33, 43.04it/s]

  2%|▏         | 1644/93492 [00:38<35:34, 43.03it/s]

  2%|▏         | 1650/93492 [00:38<35:32, 43.07it/s]

  2%|▏         | 1655/93492 [00:38<35:33, 43.04it/s]

  2%|▏         | 1662/93492 [00:38<35:33, 43.04it/s]

  2%|▏         | 1669/93492 

  3%|▎         | 2356/93492 [00:53<34:37, 43.88it/s]

  3%|▎         | 2362/93492 [00:53<34:36, 43.88it/s]

  3%|▎         | 2368/93492 [00:53<34:36, 43.89it/s]

  3%|▎         | 2373/93492 [00:54<34:36, 43.89it/s]

  3%|▎         | 2378/93492 [00:54<34:35, 43.90it/s]

  3%|▎         | 2385/93492 [00:54<34:33, 43.94it/s]

  3%|▎         | 2391/93492 [00:54<34:32, 43.95it/s]

  3%|▎         | 2397/93492 [00:54<34:32, 43.96it/s]

  3%|▎         | 2403/93492 [00:54<34:31, 43.97it/s]

  3%|▎         | 2409/93492 [00:54<34:30, 44.00it/s]

  3%|▎         | 2415/93492 [00:54<34:30, 44.00it/s]

  3%|▎         | 2421/93492 [00:55<34:29, 44.00it/s]

  3%|▎         | 2426/93492 [00:55<34:29, 44.01it/s]

  3%|▎         | 2433/93492 [00:55<34:27, 44.04it/s]

  3%|▎         | 2439/93492 [00:55<34:27, 44.05it/s]

  3%|▎         | 2445/93492 [00:55<34:26, 44.06it/s]

  3%|▎         | 2451/93492 [00:55<34:25, 44.07it/s]

  3%|▎         | 2457/93492 [00:55<34:24, 44.10it/s]

  3%|▎         | 2463/93492 

...

 98%|█████████▊| 89138/91418 [36:17<00:55, 40.93it/s]

 98%|█████████▊| 89143/91418 [36:17<00:55, 40.93it/s]

 98%|█████████▊| 89148/91418 [36:18<00:55, 40.93it/s]

 98%|█████████▊| 89153/91418 [36:18<00:55, 40.93it/s]

 98%|█████████▊| 89158/91418 [36:18<00:55, 40.93it/s]

 98%|█████████▊| 89164/91418 [36:18<00:55, 40.93it/s]

 98%|█████████▊| 89170/91418 [36:18<00:54, 40.93it/s]

 98%|█████████▊| 89175/91418 [36:18<00:54, 40.93it/s]

 98%|█████████▊| 89180/91418 [36:18<00:54, 40.93it/s]

 98%|█████████▊| 89186/91418 [36:18<00:54, 40.93it/s]

 98%|█████████▊| 89191/91418 [36:19<00:54, 40.93it/s]

 98%|█████████▊| 89196/91418 [36:19<00:54, 40.93it/s]

 98%|█████████▊| 89201/91418 [36:19<00:54, 40.93it/s]

 98%|█████████▊| 89206/91418 [36:19<00:54, 40.93it/s]

 98%|█████████▊| 89212/91418 [36:19<00:53, 40.93it/s]

 98%|█████████▊| 89217/91418 [36:19<00:53, 40.93it/s]

 98%|█████████▊| 89222/91418 [36:19<00:53, 40.93it/s]

 98%|█████████▊| 89228/91418 [36:19<00:53, 40.93it/s]

 98%|█████

 98%|█████████▊| 89880/91418 [36:34<00:37, 40.96it/s]

 98%|█████████▊| 89885/91418 [36:34<00:37, 40.96it/s]

 98%|█████████▊| 89891/91418 [36:34<00:37, 40.96it/s]

 98%|█████████▊| 89897/91418 [36:34<00:37, 40.96it/s]

 98%|█████████▊| 89903/91418 [36:35<00:36, 40.96it/s]

 98%|█████████▊| 89908/91418 [36:35<00:36, 40.96it/s]

 98%|█████████▊| 89914/91418 [36:35<00:36, 40.96it/s]

 98%|█████████▊| 89919/91418 [36:35<00:36, 40.96it/s]

 98%|█████████▊| 89924/91418 [36:35<00:36, 40.96it/s]

 98%|█████████▊| 89930/91418 [36:35<00:36, 40.96it/s]

 98%|█████████▊| 89935/91418 [36:35<00:36, 40.96it/s]

 98%|█████████▊| 89940/91418 [36:35<00:36, 40.96it/s]

 98%|█████████▊| 89946/91418 [36:35<00:35, 40.96it/s]

 98%|█████████▊| 89952/91418 [36:36<00:35, 40.96it/s]

 98%|█████████▊| 89958/91418 [36:36<00:35, 40.96it/s]

 98%|█████████▊| 89963/91418 [36:36<00:35, 40.96it/s]

 98%|█████████▊| 89969/91418 [36:36<00:35, 40.96it/s]

 98%|█████████▊| 89974/91418 [36:36<00:35, 40.96it/s]

 98%|█████

 99%|█████████▉| 90604/91418 [36:51<00:19, 40.97it/s]

 99%|█████████▉| 90609/91418 [36:51<00:19, 40.97it/s]

 99%|█████████▉| 90616/91418 [36:51<00:19, 40.97it/s]

 99%|█████████▉| 90621/91418 [36:51<00:19, 40.97it/s]

 99%|█████████▉| 90626/91418 [36:51<00:19, 40.97it/s]

 99%|█████████▉| 90631/91418 [36:51<00:19, 40.97it/s]

 99%|█████████▉| 90637/91418 [36:52<00:19, 40.97it/s]

 99%|█████████▉| 90642/91418 [36:52<00:18, 40.97it/s]

 99%|█████████▉| 90647/91418 [36:52<00:18, 40.97it/s]

 99%|█████████▉| 90653/91418 [36:52<00:18, 40.97it/s]

 99%|█████████▉| 90658/91418 [36:52<00:18, 40.97it/s]

 99%|█████████▉| 90663/91418 [36:52<00:18, 40.97it/s]

 99%|█████████▉| 90668/91418 [36:52<00:18, 40.98it/s]

 99%|█████████▉| 90673/91418 [36:52<00:18, 40.98it/s]

 99%|█████████▉| 90678/91418 [36:53<00:18, 40.98it/s]

 99%|█████████▉| 90684/91418 [36:53<00:17, 40.98it/s]

 99%|█████████▉| 90689/91418 [36:53<00:17, 40.98it/s]

 99%|█████████▉| 90694/91418 [36:53<00:17, 40.98it/s]

 99%|█████

100%|█████████▉| 91338/91418 [37:07<00:01, 41.00it/s]

100%|█████████▉| 91343/91418 [37:07<00:01, 41.00it/s]

100%|█████████▉| 91349/91418 [37:08<00:01, 41.00it/s]

100%|█████████▉| 91354/91418 [37:08<00:01, 41.00it/s]

100%|█████████▉| 91361/91418 [37:08<00:01, 41.00it/s]

100%|█████████▉| 91366/91418 [37:08<00:01, 41.00it/s]

100%|█████████▉| 91372/91418 [37:08<00:01, 41.00it/s]

100%|█████████▉| 91377/91418 [37:08<00:00, 41.00it/s]

100%|█████████▉| 91382/91418 [37:09<00:00, 40.99it/s]

100%|█████████▉| 91406/91418 [37:09<00:00, 41.00it/s]

100%|█████████▉| 91415/91418 [37:09<00:00, 41.00it/s]

100%|██████████| 91418/91418 [37:09<00:00, 41.00it/s]

got revisted_cates_top_3_df (91418, 91)
df merge cate_top_3_features_df done
process expand_cate_features done
train.shape (903653, 174)
test.shape (804684, 181)
process cate_features_fillna done


In [49]:
# Parallet groupby works well
# Merge the same fullVisitorId records into one record


def merge_group_func(df):
    def merge_one_column(x):
        new_merged_value=x.mode().values[0]
        return new_merged_value

    temp = df.apply(merge_one_column)

    return temp

def merge_duplicated_into_new_row(df):
    print()
    print('unique fullVisitorId size ',df.shape, len(df['fullVisitorId'].unique()))

    d_rows = df[df['fullVisitorId'].duplicated(keep=False)]
    revisted_df = df.loc[d_rows.index]
    unique_user_size = len(revisted_df['fullVisitorId'].unique())
    
    print('revisted_df.shape',revisted_df.shape, unique_user_size)

    new_merged_df = applyParallel(revisted_df.groupby('fullVisitorId'), merge_group_func, unique_user_size)
    print('new_merged_df.shape',new_merged_df.shape)

    df.drop(d_rows.index, inplace=True)
    
    df = pd.concat([df,new_merged_df], axis=0)
    del d_rows
    del new_merged_df
    
    print('df.shape',df.shape)

    return df
    

train = merge_duplicated_into_new_row(train)
test = merge_duplicated_into_new_row(test)
print('merge_duplicated_into_new_row done')

print()
print('train.shape', train.shape)
print('test.shape', test.shape)


unique fullVisitorId size  (903653, 174) 714167
revisted_df.shape (282978, 174) 93492




  0%|          | 0/93492 [00:00<?, ?it/s]

  0%|          | 9/93492 [00:00<23:33, 66.12it/s]

  0%|          | 25/93492 [00:00<16:21, 95.25it/s]

  0%|          | 38/93492 [00:00<15:34, 100.01it/s]

  0%|          | 53/93492 [00:00<14:39, 106.19it/s]

  0%|          | 69/93492 [00:00<14:28, 107.60it/s]

  0%|          | 79/93492 [00:00<17:56, 86.80it/s] 

  0%|          | 113/93492 [00:01<14:04, 110.51it/s]

  0%|          | 129/93492 [00:01<13:48, 112.69it/s]

  0%|          | 145/93492 [00:01<13:42, 113.53it/s]

  0%|          | 161/93492 [00:01<13:32, 114.84it/s]

  0%|          | 177/93492 [00:01<13:29, 115.34it/s]

  0%|          | 193/93492 [00:01<13:24, 115.95it/s]

  0%|          | 209/93492 [00:01<13:20, 116.57it/s]

  0%|          | 225/93492 [00:01<13:15, 117.19it/s]

  0%|          | 241/93492 [00:02<13:14, 117.42it/s]

  0%|          | 257/93492 [00:02<13:13, 117.51it/s]

  0%|          | 273/93492 [00:02<13:10, 117.97it/s]

  0%|          | 289/93492 [00:02<13:09, 118.1

  2%|▏         | 1820/93492 [00:15<13:05, 116.67it/s]

  2%|▏         | 1833/93492 [00:15<13:05, 116.73it/s]

  2%|▏         | 1845/93492 [00:15<13:05, 116.65it/s]

  2%|▏         | 1858/93492 [00:15<13:05, 116.63it/s]

  2%|▏         | 1870/93492 [00:16<13:05, 116.61it/s]

  2%|▏         | 1883/93492 [00:16<13:05, 116.65it/s]

  2%|▏         | 1895/93492 [00:16<13:05, 116.61it/s]

  2%|▏         | 1907/93492 [00:16<13:06, 116.48it/s]

  2%|▏         | 1920/93492 [00:16<13:05, 116.55it/s]

  2%|▏         | 1932/93492 [00:16<13:06, 116.46it/s]

  2%|▏         | 1947/93492 [00:16<13:05, 116.59it/s]

  2%|▏         | 1959/93492 [00:16<13:04, 116.60it/s]

  2%|▏         | 1971/93492 [00:16<13:05, 116.58it/s]

  2%|▏         | 1983/93492 [00:17<13:04, 116.58it/s]

  2%|▏         | 1995/93492 [00:17<13:04, 116.58it/s]

  2%|▏         | 2007/93492 [00:17<13:04, 116.58it/s]

  2%|▏         | 2019/93492 [00:17<13:04, 116.54it/s]

  2%|▏         | 2033/93492 [00:17<13:04, 116.58it/s]

  2%|▏    

  4%|▍         | 3582/93492 [00:30<12:44, 117.66it/s]

  4%|▍         | 3595/93492 [00:30<12:44, 117.65it/s]

  4%|▍         | 3610/93492 [00:30<12:43, 117.71it/s]

  4%|▍         | 3623/93492 [00:30<12:43, 117.74it/s]

  4%|▍         | 3636/93492 [00:30<12:43, 117.70it/s]

  4%|▍         | 3650/93492 [00:31<12:43, 117.74it/s]

  4%|▍         | 3663/93492 [00:31<12:43, 117.71it/s]

  4%|▍         | 3677/93492 [00:31<12:42, 117.76it/s]

  4%|▍         | 3690/93492 [00:31<12:42, 117.79it/s]

  4%|▍         | 3703/93492 [00:31<12:42, 117.75it/s]

  4%|▍         | 3717/93492 [00:31<12:42, 117.81it/s]

  4%|▍         | 3730/93492 [00:31<12:41, 117.81it/s]

  4%|▍         | 3743/93492 [00:31<12:41, 117.82it/s]

  4%|▍         | 3757/93492 [00:31<12:41, 117.84it/s]

  4%|▍         | 3770/93492 [00:31<12:41, 117.86it/s]

  4%|▍         | 3783/93492 [00:32<12:41, 117.85it/s]

  4%|▍         | 3797/93492 [00:32<12:40, 117.91it/s]

  4%|▍         | 3810/93492 [00:32<12:40, 117.89it/s]

  4%|▍    

  6%|▌         | 5319/93492 [00:45<12:29, 117.57it/s]

  6%|▌         | 5331/93492 [00:45<12:30, 117.54it/s]

  6%|▌         | 5344/93492 [00:45<12:29, 117.55it/s]

  6%|▌         | 5356/93492 [00:45<12:29, 117.53it/s]

  6%|▌         | 5369/93492 [00:45<12:29, 117.53it/s]

  6%|▌         | 5381/93492 [00:45<12:29, 117.53it/s]

  6%|▌         | 5393/93492 [00:45<12:29, 117.51it/s]

  6%|▌         | 5406/93492 [00:45<12:29, 117.53it/s]

  6%|▌         | 5418/93492 [00:46<12:29, 117.50it/s]

  6%|▌         | 5431/93492 [00:46<12:29, 117.52it/s]

  6%|▌         | 5443/93492 [00:46<12:29, 117.49it/s]

  6%|▌         | 5457/93492 [00:46<12:29, 117.51it/s]

  6%|▌         | 5469/93492 [00:46<12:29, 117.50it/s]

  6%|▌         | 5481/93492 [00:46<12:29, 117.49it/s]

  6%|▌         | 5495/93492 [00:46<12:28, 117.50it/s]

  6%|▌         | 5507/93492 [00:46<12:28, 117.49it/s]

  6%|▌         | 5520/93492 [00:46<12:28, 117.51it/s]

  6%|▌         | 5532/93492 [00:47<12:28, 117.48it/s]

  6%|▌    

...

 92%|█████████▏| 84419/91418 [12:45<01:03, 110.32it/s]

 92%|█████████▏| 84433/91418 [12:45<01:03, 110.33it/s]

 92%|█████████▏| 84447/91418 [12:45<01:03, 110.33it/s]

 92%|█████████▏| 84460/91418 [12:45<01:03, 110.33it/s]

 92%|█████████▏| 84473/91418 [12:45<01:02, 110.33it/s]

 92%|█████████▏| 84487/91418 [12:45<01:02, 110.34it/s]

 92%|█████████▏| 84500/91418 [12:45<01:02, 110.34it/s]

 92%|█████████▏| 84515/91418 [12:45<01:02, 110.34it/s]

 92%|█████████▏| 84529/91418 [12:46<01:02, 110.35it/s]

 92%|█████████▏| 84543/91418 [12:46<01:02, 110.35it/s]

 92%|█████████▏| 84557/91418 [12:46<01:02, 110.35it/s]

 93%|█████████▎| 84570/91418 [12:46<01:02, 110.35it/s]

 93%|█████████▎| 84584/91418 [12:46<01:01, 110.36it/s]

 93%|█████████▎| 84599/91418 [12:46<01:01, 110.36it/s]

 93%|█████████▎| 84613/91418 [12:46<01:01, 110.36it/s]

 93%|█████████▎| 84627/91418 [12:46<01:01, 110.37it/s]

 93%|█████████▎| 84641/91418 [12:46<01:01, 110.37it/s]

 93%|█████████▎| 84655/91418 [12:47<01:01, 110.3

 94%|█████████▍| 86330/91418 [12:59<00:45, 110.71it/s]

 94%|█████████▍| 86346/91418 [12:59<00:45, 110.72it/s]

 94%|█████████▍| 86360/91418 [12:59<00:45, 110.72it/s]

 94%|█████████▍| 86374/91418 [13:00<00:45, 110.72it/s]

 94%|█████████▍| 86388/91418 [13:00<00:45, 110.73it/s]

 95%|█████████▍| 86402/91418 [13:00<00:45, 110.73it/s]

 95%|█████████▍| 86417/91418 [13:00<00:45, 110.73it/s]

 95%|█████████▍| 86431/91418 [13:00<00:45, 110.73it/s]

 95%|█████████▍| 86445/91418 [13:00<00:44, 110.74it/s]

 95%|█████████▍| 86459/91418 [13:00<00:44, 110.74it/s]

 95%|█████████▍| 86473/91418 [13:00<00:44, 110.74it/s]

 95%|█████████▍| 86487/91418 [13:00<00:44, 110.75it/s]

 95%|█████████▍| 86501/91418 [13:01<00:44, 110.75it/s]

 95%|█████████▍| 86514/91418 [13:01<00:44, 110.75it/s]

 95%|█████████▍| 86529/91418 [13:01<00:44, 110.75it/s]

 95%|█████████▍| 86543/91418 [13:01<00:44, 110.75it/s]

 95%|█████████▍| 86557/91418 [13:01<00:43, 110.76it/s]

 95%|█████████▍| 86570/91418 [13:01<00:43, 110.7

 97%|█████████▋| 88223/91418 [13:14<00:28, 111.06it/s]

 97%|█████████▋| 88236/91418 [13:14<00:28, 111.06it/s]

 97%|█████████▋| 88248/91418 [13:14<00:28, 111.06it/s]

 97%|█████████▋| 88260/91418 [13:14<00:28, 111.06it/s]

 97%|█████████▋| 88273/91418 [13:14<00:28, 111.06it/s]

 97%|█████████▋| 88285/91418 [13:14<00:28, 111.06it/s]

 97%|█████████▋| 88298/91418 [13:15<00:28, 111.06it/s]

 97%|█████████▋| 88310/91418 [13:15<00:27, 111.06it/s]

 97%|█████████▋| 88324/91418 [13:15<00:27, 111.06it/s]

 97%|█████████▋| 88337/91418 [13:15<00:27, 111.06it/s]

 97%|█████████▋| 88350/91418 [13:15<00:27, 111.06it/s]

 97%|█████████▋| 88366/91418 [13:15<00:27, 111.07it/s]

 97%|█████████▋| 88382/91418 [13:15<00:27, 111.07it/s]

 97%|█████████▋| 88397/91418 [13:15<00:27, 111.08it/s]

 97%|█████████▋| 88411/91418 [13:15<00:27, 111.08it/s]

 97%|█████████▋| 88426/91418 [13:16<00:26, 111.08it/s]

 97%|█████████▋| 88440/91418 [13:16<00:26, 111.08it/s]

 97%|█████████▋| 88454/91418 [13:16<00:26, 111.0

 99%|█████████▊| 90095/91418 [13:29<00:11, 111.36it/s]

 99%|█████████▊| 90108/91418 [13:29<00:11, 111.36it/s]

 99%|█████████▊| 90123/91418 [13:29<00:11, 111.36it/s]

 99%|█████████▊| 90137/91418 [13:29<00:11, 111.36it/s]

 99%|█████████▊| 90151/91418 [13:29<00:11, 111.37it/s]

 99%|█████████▊| 90164/91418 [13:29<00:11, 111.37it/s]

 99%|█████████▊| 90179/91418 [13:29<00:11, 111.37it/s]

 99%|█████████▊| 90193/91418 [13:29<00:10, 111.37it/s]

 99%|█████████▊| 90207/91418 [13:29<00:10, 111.38it/s]

 99%|█████████▊| 90221/91418 [13:30<00:10, 111.38it/s]

 99%|█████████▊| 90235/91418 [13:30<00:10, 111.38it/s]

 99%|█████████▊| 90249/91418 [13:30<00:10, 111.38it/s]

 99%|█████████▊| 90263/91418 [13:30<00:10, 111.39it/s]

 99%|█████████▉| 90277/91418 [13:30<00:10, 111.39it/s]

 99%|█████████▉| 90291/91418 [13:30<00:10, 111.39it/s]

 99%|█████████▉| 90306/91418 [13:30<00:09, 111.39it/s]

 99%|█████████▉| 90321/91418 [13:30<00:09, 111.40it/s]

 99%|█████████▉| 90335/91418 [13:30<00:09, 111.4

new_merged_df.shape (91418, 181)
df.shape (617242, 181)
merge_duplicated_into_new_row done

train.shape (714167, 174)
test.shape (617242, 181)


In [50]:
new_cate_features = [] 
for col in cate_features:
    new_cate_features.append(col + '_top_1')
    new_cate_features.append(col + '_top_2')
    new_cate_features.append(col + '_top_3')
    
cate_features += new_cate_features


new_numeric_features = []
for col in numeric_features:
    new_numeric_features.append(col+'_' +'min')
    new_numeric_features.append(col+'_' +'max')
    new_numeric_features.append(col+'_' +'mean')
    new_numeric_features.append(col+'_' +'median')
    
numeric_features += new_numeric_features

print()
print('cate_features', len(cate_features), cate_features)
print('numeric_features', len(numeric_features), numeric_features)


cate_features 120 ['channelGrouping', 'date', 'year', 'month', 'day', 'week', 'weekofyear', 'dayofweek', 'quarter', 'month_start', 'month_end', 'browser', 'operatingSystem', 'isMobile', 'deviceCategory', 'continent', 'subContinent', 'country', 'region', 'metro', 'city', 'networkDomain', 'campaign', 'source', 'medium', 'keyword', 'adwordsClickInfo_gclId_prefix', 'adwordsClickInfo_slot', 'adwordsClickInfo_gclId', 'adwordsClickInfo_adNetworkType', 'channelGrouping_top_1', 'channelGrouping_top_2', 'channelGrouping_top_3', 'date_top_1', 'date_top_2', 'date_top_3', 'year_top_1', 'year_top_2', 'year_top_3', 'month_top_1', 'month_top_2', 'month_top_3', 'day_top_1', 'day_top_2', 'day_top_3', 'week_top_1', 'week_top_2', 'week_top_3', 'weekofyear_top_1', 'weekofyear_top_2', 'weekofyear_top_3', 'dayofweek_top_1', 'dayofweek_top_2', 'dayofweek_top_3', 'quarter_top_1', 'quarter_top_2', 'quarter_top_3', 'month_start_top_1', 'month_start_top_2', 'month_start_top_3', 'month_end_top_1', 'month_end_top_

In [55]:
from keras.layers import Input, Dense, concatenate, Dropout, Embedding, Flatten
from keras.models import Model
from keras import optimizers

def get_model():
    input_cate = Input((len(cate_features),))
    input_numeric = Input((len(numeric_features),))
    
    x_cate = Embedding(100000, 10)(input_cate)
    x_cate = Flatten()(x_cate)
    x_cate = Dropout(0.2)(x_cate)
    x_cate = Dense(100, activation='relu')(x_cate)
    
    
    x_numeric = Dense(100, activation='relu')(input_numeric)
    x_numeric = Dropout(0.2)(x_numeric)
    
    x = concatenate([x_cate,x_numeric])
    
    x = Dense(100, activation='relu')(x)
    x = Dropout(0.2)(x)
    
    output = Dense(1, kernel_initializer='normal')(x)
    
    model = Model(inputs=[input_cate,input_numeric], outputs=output)
    model.compile(optimizer=optimizers.Adam(), loss='mean_squared_error', metrics=['mse'])
    
    return model
    
    
model = get_model()
print(model.summary())
model.fit([train[cate_features], train[numeric_features]], train[target], validation_split=0.2, epochs=2, batch_size=100)
print('model.fit done')


print('test.shape',test.shape)
predict_test = model.predict([test[cate_features], test[numeric_features]],verbose=1)

test['PredictedLogRevenue'] = predict_test

test[['fullVisitorId','PredictedLogRevenue']].to_csv('GStore_keras_baseline.csv', index=False)
print(test.shape)

print('predict done')

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_9 (InputLayer)            (None, 120)          0                                            
__________________________________________________________________________________________________
embedding_5 (Embedding)         (None, 120, 10)      1000000     input_9[0][0]                    
__________________________________________________________________________________________________
flatten_5 (Flatten)             (None, 1200)         0           embedding_5[0][0]                
__________________________________________________________________________________________________
input_10 (InputLayer)           (None, 50)           0                                            
__________________________________________________________________________________________________
dropout_13